In [1]:
import math
import robin_stocks.robinhood as rh
import pandas as pd
import requests
from datetime import datetime as dt
import time

username = 'jizhaobridgeport@gmail.com'
password = '12345shift'

def login():
    rh.login(username, password)
def get_stop(stock):# pivotpoints
        from datetime import datetime as dt
        import datetime
        import dateutil
        today = datetime.datetime.today()
        delta = dateutil.relativedelta.relativedelta(months=1)
        end = (today-datetime.timedelta(1)).strftime('%Y-%m-%d') 
        start = (today - delta).strftime('%Y-%m-%d')

        import requests
        api_key = '86dd63f6b8ae774b061232685b78eb52'
        from datetime import datetime
        bs = requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/{ticker}?from={start}&to={end}&apikey={api_key}').json()['historical']
        
        # Print the raw data to check
        print(f"Raw data for {stock}:")
        print(bs)
        
        stock = pd.DataFrame(bs)
        stock =stock[['date','open','high','low','close','volume']]
        stock = stock.rename(columns = {'date':'Date', 'open':'Open', 'high':'High','low':'Low', 'close':'Close', 'volume':'volume'})
        stock = stock.set_index('Date')
        stock= stock.sort_index()
        last_day = stock.iloc[-1].to_frame().T
        not_pivots = last_day.columns
        last_day['center_gravity'] = (last_day['High'] + last_day['Low'] + last_day['Close'])/3
        
        # Print calculations
        print("\nCalculations:")
        print(f"Center of Gravity: {last_day['center_gravity'].values[0]}")
        
        last_day['vol_up1'] = 2*last_day['center_gravity'] - last_day['Low']
        print(f"Volatility Up 1: {last_day['vol_up1'].values[0]}")
        
        last_day['vol_down1'] = 2*last_day['center_gravity'] - last_day['High']
        print(f"Volatility Down 1: {last_day['vol_down1'].values[0]}")
        
        last_day['vol_up2'] = last_day['center_gravity'] + (last_day['High'] - last_day['Low'])
        print(f"Volatility Up 2: {last_day['vol_up2'].values[0]}")
        
        last_day['vol_down2'] = last_day['center_gravity'] - (last_day['High'] - last_day['Low'])
        print(f"Volatility Down 2: {last_day['vol_down2'].values[0]}")
        
        last_day['vol_up3'] = last_day['center_gravity'] + 2*(last_day['High'] - last_day['Low'])
        print(f"Volatility Up 3: {last_day['vol_up3'].values[0]}")
        
        last_day['vol_down3'] = last_day['center_gravity'] - 2*(last_day['High'] - last_day['Low'])
        print(f"Volatility Down 3: {last_day['vol_down3'].values[0]}")
        
        last_day['stop_loss'] = (last_day['vol_down2'] + last_day['vol_down3'])/2
        print(f"Initial Stop Loss: {last_day['stop_loss'].values[0]}")
        
        last_day['stop_loss_pct'] = (last_day['Close'] - last_day['stop_loss'])/last_day['Close']*100
        print(f"Initial Stop Loss Percentage: {last_day['stop_loss_pct'].values[0]}%")
        
        if last_day['stop_loss_pct'][-1] >3.5:
            last_day['stop_loss'][-1]= (last_day['vol_down1'][-1] + last_day['Close'][-1])/2
            print(f"Adjusted Stop Loss (because percentage > 3.5%): {last_day['stop_loss'].values[0]}")
        
        return last_day

    
    
def get_trailing_stop_percentage(stock):
    stop_price = get_stop(stock)['stop_loss'][0]
    current_price = all_data1['price'][stock]
    trailing_percentage = (current_price - stop_price) / current_price
    
    # Print statements for debugging
    print(f"\nStock: {stock}")
    print(f"Current Price: ${current_price}")
    print(f"Stop Price from get_stop(): ${stop_price}")
    print(f"Trailing Percentage (from difference): {trailing_percentage*100:.2f}%")
    
    return trailing_percentage * 0.2  # Use 20% of the calculated stop percentage

login()

sold_half = set()  # Track stocks that we have sold half of


while True:
    my_stocks = rh.build_holdings()
    df = pd.DataFrame(my_stocks).T
    df1 = df[['price', 'quantity', 'average_buy_price', 'percent_change']]
    stock = df1.index.tolist()
    all_data = pd.DataFrame()

    for ticker in stock:
        print(ticker)
        last_day = get_stop(ticker)
        all_data = pd.concat([all_data, last_day], axis=0)

    all_data = all_data[['stop_loss']]
    all_data1 = df1.merge(all_data, left_index=True, right_index=True)
    all_data1['price'] = all_data1['price'].astype(float)
    all_data1['pct_cha'] = ((all_data1['price'] - all_data1['stop_loss']) / all_data1['price']) * 100

    import random
    x = random.random()
    y = float((x + 5) / 100)
    z = float((10 - x) / 100)
    all_data1['average_buy_price'] = all_data1['average_buy_price'].astype(float)
    all_data1['target_price1'] = all_data1['average_buy_price'] * (1 + y)
    all_data1['target_price2'] = all_data1['average_buy_price'] * (1 + z)

    trailing_stop_percentages = {}
    for s in all_data1.index.tolist():
        current_price = all_data1['price'][s]
        trailing_stop_pct = get_trailing_stop_percentage(s)
        trailing_stop_price = current_price * (1 - trailing_stop_pct)

        # Additional print statement for debugging
        print(f"Final Trailing Stop Price for {s}: ${trailing_stop_price:.2f}")
    
    
    for s in all_data1.index.tolist():
        current_price = all_data1['price'][s]
        average_price = all_data1['average_buy_price'][s]
        quantity = float(all_data1['quantity'][s])
        trailing_stop_price = current_price * (1 - trailing_stop_percentages[s])
        loss_pct = (current_price - trailing_stop_price) / current_price * 100
        gain_pct = (current_price - average_price) / average_price * 100

        if current_price >= all_data1['target_price1'][s] and s not in sold_half:
            print(f"Would sell half of {s} at market price with a gain of {gain_pct:.2f}%.")
            sold_half.add(s)

        elif current_price >= all_data1['target_price2'][s]:
            print(f"Would sell all of {s} at market price with a gain of {gain_pct:.2f}%.")
        
        elif current_price <= trailing_stop_price:
            print(f"Trailing stop would be triggered for {s}, selling all at market price. Stop Price: ${trailing_stop_price:.2f}, Loss: {loss_pct:.2f}%.")

    time.sleep(3600)

400 Client Error: Bad Request for url: https://api.robinhood.com/fundamentals/?symbols=SBRCY
400 Client Error: Bad Request for url: https://api.robinhood.com/quotes/?symbols=SBRCY
DIS
Raw data for DIS:
[{'date': '2023-10-10', 'open': 84.79, 'high': 85.285, 'low': 83.93, 'close': 84.99, 'adjClose': 84.99, 'volume': 9450609, 'unadjustedVolume': 9450600, 'change': 0.2, 'changePercent': 0.23588, 'vwap': 84.9, 'label': 'October 10, 23', 'changeOverTime': 0.0023588}, {'date': '2023-10-09', 'open': 84.3, 'high': 84.88, 'low': 83.13, 'close': 84.7, 'adjClose': 84.7, 'volume': 13604405, 'unadjustedVolume': 13604400, 'change': 0.4, 'changePercent': 0.4745, 'vwap': 84.2, 'label': 'October 09, 23', 'changeOverTime': 0.004745}, {'date': '2023-10-06', 'open': 81.05, 'high': 83.53, 'low': 80.49, 'close': 82.94, 'adjClose': 82.94, 'volume': 15391073, 'unadjustedVolume': 15375100, 'change': 1.89, 'changePercent': 2.33, 'vwap': 82.34, 'label': 'October 06, 23', 'changeOverTime': 0.0233}, {'date': '2023-

Raw data for GOOGL:
[{'date': '2023-10-10', 'open': 138.5, 'high': 139.72, 'low': 137.33, 'close': 138.06, 'adjClose': 138.06, 'volume': 27775413, 'unadjustedVolume': 27786600, 'change': -0.44, 'changePercent': -0.31769, 'vwap': 138.53, 'label': 'October 10, 23', 'changeOverTime': -0.0031769}, {'date': '2023-10-09', 'open': 136.94, 'high': 138.94, 'low': 135.61, 'close': 138.42, 'adjClose': 138.42, 'volume': 19278070, 'unadjustedVolume': 19278100, 'change': 1.48, 'changePercent': 1.08, 'vwap': 137.85, 'label': 'October 09, 23', 'changeOverTime': 0.0108}, {'date': '2023-10-06', 'open': 134.01, 'high': 138.155, 'low': 134.01, 'close': 137.58, 'adjClose': 137.58, 'volume': 27597598, 'unadjustedVolume': 27583200, 'change': 3.57, 'changePercent': 2.66, 'vwap': 136.91, 'label': 'October 06, 23', 'changeOverTime': 0.0266}, {'date': '2023-10-05', 'open': 135.07, 'high': 135.49, 'low': 133.45, 'close': 135.07, 'adjClose': 135.07, 'volume': 19832615, 'unadjustedVolume': 19832600, 'change': 0, 'c

Raw data for TSLA:
[{'date': '2023-10-10', 'open': 257.75, 'high': 268.94, 'low': 257.65, 'close': 263.62, 'adjClose': 263.62, 'volume': 122656030, 'unadjustedVolume': 122656000, 'change': 5.87, 'changePercent': 2.28, 'vwap': 264.95, 'label': 'October 10, 23', 'changeOverTime': 0.0228}, {'date': '2023-10-09', 'open': 255.31, 'high': 261.36, 'low': 252.05, 'close': 259.67, 'adjClose': 259.67, 'volume': 101377947, 'unadjustedVolume': 101377900, 'change': 4.36, 'changePercent': 1.71, 'vwap': 256.32, 'label': 'October 09, 23', 'changeOverTime': 0.0171}, {'date': '2023-10-06', 'open': 253.98, 'high': 261.65, 'low': 250.65, 'close': 260.53, 'adjClose': 260.53, 'volume': 118108312, 'unadjustedVolume': 117947000, 'change': 6.55, 'changePercent': 2.58, 'vwap': 256.32, 'label': 'October 06, 23', 'changeOverTime': 0.0258}, {'date': '2023-10-05', 'open': 260, 'high': 263.6, 'low': 256.25, 'close': 260.05, 'adjClose': 260.05, 'volume': 119159214, 'unadjustedVolume': 119159200, 'change': 0.05, 'chan

Raw data for AAPL:
[{'date': '2023-10-10', 'open': 178.1, 'high': 179.72, 'low': 177.95, 'close': 178.39, 'adjClose': 178.39, 'volume': 43698019, 'unadjustedVolume': 43698000, 'change': 0.29, 'changePercent': 0.16283, 'vwap': 178.69, 'label': 'October 10, 23', 'changeOverTime': 0.0016283}, {'date': '2023-10-09', 'open': 176.81, 'high': 179.05, 'low': 175.8, 'close': 178.99, 'adjClose': 178.99, 'volume': 42344772, 'unadjustedVolume': 42390800, 'change': 2.18, 'changePercent': 1.23, 'vwap': 177.87, 'label': 'October 09, 23', 'changeOverTime': 0.0123}, {'date': '2023-10-06', 'open': 173.8, 'high': 177.99, 'low': 173.18, 'close': 177.49, 'adjClose': 177.49, 'volume': 57266675, 'unadjustedVolume': 57224100, 'change': 3.69, 'changePercent': 2.12, 'vwap': 176.34, 'label': 'October 06, 23', 'changeOverTime': 0.0212}, {'date': '2023-10-05', 'open': 173.79, 'high': 175.45, 'low': 172.68, 'close': 174.91, 'adjClose': 174.91, 'volume': 48527918, 'unadjustedVolume': 48527900, 'change': 1.12, 'chang

Raw data for JNJ:
[{'date': '2023-10-10', 'open': 158.38, 'high': 159.27, 'low': 157.9, 'close': 158.36, 'adjClose': 158.36, 'volume': 5273531, 'unadjustedVolume': 5273500, 'change': -0.02, 'changePercent': -0.01262786, 'vwap': 158.49, 'label': 'October 10, 23', 'changeOverTime': -0.0001262786}, {'date': '2023-10-09', 'open': 157.18, 'high': 158.88, 'low': 157.09, 'close': 158.54, 'adjClose': 158.54, 'volume': 4414322, 'unadjustedVolume': 4414100, 'change': 1.36, 'changePercent': 0.86525, 'vwap': 158.16, 'label': 'October 09, 23', 'changeOverTime': 0.0086525}, {'date': '2023-10-06', 'open': 157.08, 'high': 158.3, 'low': 156.59, 'close': 157.64, 'adjClose': 157.64, 'volume': 5802226, 'unadjustedVolume': 5801100, 'change': 0.56, 'changePercent': 0.35651, 'vwap': 157.61, 'label': 'October 06, 23', 'changeOverTime': 0.0035651}, {'date': '2023-10-05', 'open': 156.27, 'high': 158.0399, 'low': 156.07, 'close': 157.14, 'adjClose': 157.14, 'volume': 5993541, 'unadjustedVolume': 5993300, 'change

...

Raw data for SHOP:
[{'date': '2023-10-12', 'open': 54.5, 'high': 55.03, 'low': 52.92, 'close': 53.33, 'adjClose': 53.33, 'volume': 10722626, 'unadjustedVolume': 10450359, 'change': -1.17, 'changePercent': -2.15, 'vwap': 53.95, 'label': 'October 12, 23', 'changeOverTime': -0.0215}, {'date': '2023-10-11', 'open': 55.51, 'high': 55.6383, 'low': 53.71, 'close': 54.24, 'adjClose': 54.24, 'volume': 8505693, 'unadjustedVolume': 8505700, 'change': -1.27, 'changePercent': -2.29, 'vwap': 54.51, 'label': 'October 11, 23', 'changeOverTime': -0.0229}, {'date': '2023-10-10', 'open': 53.73, 'high': 55.5891, 'low': 53.56, 'close': 55.08, 'adjClose': 55.08, 'volume': 9833977, 'unadjustedVolume': 9834000, 'change': 1.35, 'changePercent': 2.51, 'vwap': 55.11, 'label': 'October 10, 23', 'changeOverTime': 0.0251}, {'date': '2023-10-09', 'open': 52.45, 'high': 53.93, 'low': 52.06, 'close': 53.51, 'adjClose': 53.51, 'volume': 9709353, 'unadjustedVolume': 9709400, 'change': 1.06, 'changePercent': 2.02, 'vwap'

Raw data for GS:
[{'date': '2023-10-12', 'open': 314.15, 'high': 314.25, 'low': 308.02, 'close': 309.85, 'adjClose': 309.85, 'volume': 1647055, 'unadjustedVolume': 1286772, 'change': -4.3, 'changePercent': -1.37, 'vwap': 310.42, 'label': 'October 12, 23', 'changeOverTime': -0.0137}, {'date': '2023-10-11', 'open': 315.43, 'high': 316.63, 'low': 311.6, 'close': 313.02, 'adjClose': 313.02, 'volume': 1672491, 'unadjustedVolume': 1672500, 'change': -2.41, 'changePercent': -0.76404, 'vwap': 313.07, 'label': 'October 11, 23', 'changeOverTime': -0.0076404}, {'date': '2023-10-10', 'open': 314.47, 'high': 316.85, 'low': 312.29, 'close': 314.77, 'adjClose': 314.77, 'volume': 1194030, 'unadjustedVolume': 1193800, 'change': 0.3, 'changePercent': 0.09539861, 'vwap': 314.96, 'label': 'October 10, 23', 'changeOverTime': 0.0009539861}, {'date': '2023-10-09', 'open': 308.9, 'high': 313.4761, 'low': 308.37, 'close': 312.61, 'adjClose': 312.61, 'volume': 1094602, 'unadjustedVolume': 1094400, 'change': 3.7

Raw data for INTU:
[{'date': '2023-10-12', 'open': 545.09, 'high': 550.12, 'low': 540.62, 'close': 543.41, 'adjClose': 543.41, 'volume': 1507267, 'unadjustedVolume': 1242783, 'change': -1.68, 'changePercent': -0.30821, 'vwap': 544.92, 'label': 'October 12, 23', 'changeOverTime': -0.0030821}, {'date': '2023-10-11', 'open': 541.65, 'high': 544.61, 'low': 536.76, 'close': 541.58, 'adjClose': 541.58, 'volume': 884180, 'unadjustedVolume': 884200, 'change': -0.07, 'changePercent': -0.01292347, 'vwap': 540.5, 'label': 'October 11, 23', 'changeOverTime': -0.0001292347}, {'date': '2023-10-10', 'open': 532.15, 'high': 545.26, 'low': 530.66, 'close': 540.11, 'adjClose': 540.11, 'volume': 1369522, 'unadjustedVolume': 1369300, 'change': 7.96, 'changePercent': 1.5, 'vwap': 540.95, 'label': 'October 10, 23', 'changeOverTime': 0.015}, {'date': '2023-10-09', 'open': 527.76, 'high': 535.55, 'low': 526.25, 'close': 534.91, 'adjClose': 534.91, 'volume': 1047706, 'unadjustedVolume': 1047700, 'change': 7.15

503 Server Error: Service Unavailable for url: https://api.robinhood.com/portfolios/


KeyError: "None of [Index(['price', 'quantity', 'average_buy_price', 'percent_change'], dtype='object')] are in the [columns]"